In [1]:
#import sys
#!{sys.executable} -m pip install xgboost

#import sys
#!{sys.executable} -m pip install tsfresh

In [2]:
import numpy as np
import pandas as pd
%matplotlib inline
import matplotlib.pyplot as plt

from sklearn.model_selection import train_test_split,KFold
from sklearn.ensemble import ExtraTreesClassifier,RandomForestClassifier,GradientBoostingClassifier
from sklearn.metrics import classification_report, log_loss
from sklearn.metrics import confusion_matrix
from win32api import GetSystemMetrics
import seaborn as sns
import math
import time

import random

random.seed(12345)

pd.options.display.max_columns = 100
start = time.time()

In [3]:
path = './'
name = ''
out_name = path + name + 'submission_py.csv'
train_file_name = 'train_sample.csv'
test_file_name = 'test_sample.csv'

In [4]:

import itertools

def plot_confusion_matrix(cm, classes,
                          normalize=False,
                          title='Confusion matrix',
                          doprint=True,
                          cmap=plt.cm.Blues):
    """
    This function prints and plots the confusion matrix.
    Normalization can be applied by setting `normalize=True`.
    """
    if normalize:
        cm = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
        print("Normalized confusion matrix")
    else:
        print('Confusion matrix, without normalization')

    if doprint:
        print(cm)

    plt.imshow(cm, interpolation='nearest', cmap=cmap)
    plt.title(title)
    plt.colorbar()
    tick_marks = np.arange(len(classes))
    plt.xticks(tick_marks, classes, rotation=45)
    plt.yticks(tick_marks, classes)

    fmt = '.2f' if normalize else 'd'
    thresh = cm.max() / 2.
    if doprint:
        for i, j in itertools.product(range(cm.shape[0]), range(cm.shape[1])):
            plt.text(j, i, format(cm[i, j], fmt),
                     horizontalalignment="center",
                     color="white" if cm[i, j] > thresh else "black")

    plt.tight_layout()
    plt.ylabel('True label')
    plt.xlabel('Predicted label')

In [5]:
# Features calculations
def get_relevant_columns_starts(df,name):
    return [col for col in df if col.startswith(name)]
    
def calcFeatureParParam(df,name):
    filter_cols = get_relevant_columns_starts(df,name)
    df['max_'+name] = df[filter_cols].max(axis=1)
    df['min_'+name] = df[filter_cols].min(axis=1)
    df['median_'+name] = df[filter_cols].median(axis=1)
    df['std_'+name] = df[filter_cols].std(axis=1)
    df['mean_'+name] = df[filter_cols].mean(axis=1)
    
def calcV(df):
    for i in range(30):
        df['V_'+str(i)]=(df['velX_'+str(i)]**2)+(df['velY_'+str(i)]**2)+(df['velZ_'+str(i)]**2)
        df['V_'+str(i)].apply(math.sqrt)
        
    
def calcFeatures(df):
    calcFeatureParParam(df,'posX')
    calcFeatureParParam(df,'posY')
    calcFeatureParParam(df,'posZ')
    calcFeatureParParam(df,'velX')
    calcFeatureParParam(df,'velY')
    calcFeatureParParam(df,'velZ')
    calcV(df)

In [6]:
# Normalize data

def normalizeStandardParParam(df,name):
    filter_cols = get_relevant_columns_starts(df,name)
    values = df[filter_cols].values.flatten()
    values = values[~np.isnan(values)]
    mean = values.mean()
    std = values.std()
    df[filter_cols]=(df[filter_cols]-mean)/std
    
def normalizeMinMax(df, name):
    filter_cols = get_relevant_columns_starts(df,name)
    values = df[filter_cols].values.flatten()
    values = values[~np.isnan(values)]
    min = values.min()
    max = values.max()
    df[filter_cols]=(df[filter_cols]-min)/(max-min)
    

def normalizeAll(df):
    normalizeStandardParParam(df,'posX')
    normalizeStandardParParam(df,'posY')
    normalizeStandardParParam(df,'posZ')
    normalizeStandardParParam(df,'velX')
    normalizeStandardParParam(df,'velY')
    normalizeStandardParParam(df,'velZ')



In [7]:
# read data

train_data = pd.read_csv(path + name + train_file_name)
test_data = pd.read_csv(path + name + test_file_name)


In [8]:
print(train_data.shape)
print(test_data.shape)

(11, 213)
(11, 211)


In [9]:
# Data by classes exploriation 
train_data['class'].value_counts().sort_index()

1     1
3     2
8     1
13    1
14    2
16    1
18    1
20    1
21    1
Name: class, dtype: int64

In [10]:
# Normalize data and fill NaN
#normalizeAll(train_data)

In [11]:
# Features extraction
#calcFeatures(train_data)
#train_data.head(20).to_csv(path + 'features.csv')

In [12]:
# Tsfreah

from tsfresh.feature_extraction import ComprehensiveFCParameters
from tsfresh import extract_features

def changeDataStructure(df):
    columns_names = ['Id','Time', 'posX', 'posY', 'posZ', 'velX', 'velY', 'velZ']
    new_df = pd.DataFrame(columns=columns_names)
    for index, row in df.iterrows():
        for i in range(0,30):
            indexes = ['Id', 'Time_'+str(i), 'posX_'+str(i), 'posY_'+str(i), 'posZ_'+str(i), 'velX_'+str(i), 'velY_'+str(i), 'velZ_'+str(i)]
            values = index + row[indexes].values
            values[0] = index
            new_df = new_df.append(pd.Series(values, index=new_df.columns ), ignore_index=True)
    return new_df.dropna(thresh=2)


def calcFeaturesByTsfresh(df):
    new_df = changeDataStructure(df)
    #settings = ComprehensiveFCParameters()
    #extract_features(new_df, column_id="Id", default_fc_parameters=settings)
    extracted_features = extract_features(new_df, column_id="Id", column_sort="Time")
    print(extracted_features)

                             
calcFeaturesByTsfresh(train_data)
    

C:\Users\hgabayan\AppData\Local\Continuum\anaconda3\lib\site-packages\pandas\core\series.py:851: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self.loc[key]
Feature Extraction:   0%|                                                                       | 0/10 [00:00<?, ?it/s]

TypeError: 1st argument must be a real sequence 2

# Feature exploriation

In [ ]:
train_data['class'].value_counts()
corr = train_data.corr()

# plot the heatmap
width = GetSystemMetrics(0)
height = GetSystemMetrics(1)

fig = plt.figure(figsize=(width / 70., height / 70.), dpi=1500)
sns.heatmap(corr, xticklabels=corr.columns, yticklabels=corr.columns, square=True)
plt.savefig('features Heat map.png')
#plt.show(block=False)


In [ ]:
# Fetures selection

In [ ]:
X = train_data.iloc[:,1:].drop(['targetName', 'class'], axis=1).as_matrix()
y = train_data[['class']].as_matrix()

print(X.shape)
print(y.shape)

C:\Users\hgabayan\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  """Entry point for launching an IPython kernel.
C:\Users\hgabayan\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  


(28746, 270)
(28746, 1)


# Test XGBoost on first 5 seconds

In [ ]:
X_train, X_val, y_train, y_val = train_test_split(X, y, test_size=0.05)
print(X_train.shape)
print(X_val.shape)


(27308, 270)
(1438, 270)


In [ ]:
%%time
from xgboost import XGBClassifier
gbc = XGBClassifier(objective='multi:softprob',
                    learning_rate=0.2,
                    subsample=0.7,
                    colsample_bytree=0.9,
                    colsample_bylevel=0.7,
                    max_depth=5,
                    nthread=4,
                    n_estimators=50,
                    seed=1234)

gbc.fit(X_train,y_train)
pred = gbc.predict(X_val)
print(classification_report(y_pred=pred,y_true=y_val))
pred_proba = gbc.predict_proba(X_val)
print('log_loss: {}'.format(log_loss(y_pred=pred_proba,y_true=y_val)))


C:\Users\hgabayan\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\preprocessing\label.py:219: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
C:\Users\hgabayan\AppData\Local\Continuum\anaconda3\lib\site-packages\sklearn\preprocessing\label.py:252: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


In [ ]:
cnf_matrix = confusion_matrix(y_val, pred)
plt.figure()
classes = range(0,25)
plot_confusion_matrix(cnf_matrix, classes, normalize=True, doprint=False, title='Normalized confusion matrix')

In [ ]:
# submit 
#normalizeAll(test_data)
#calcFeatures(test_data)
Xt = test_data.iloc[:,1:].as_matrix()
print(Xt.shape)
pred = gbc.predict(Xt)
pred = pred.astype(int)
df = pd.DataFrame(pred)
df.to_csv(out_name, header=False)

In [ ]:
#compress result file
import gzip

in_data = open(out_name, "rb").read()
out_gz = out_name+".gz"
gzf = gzip.open(out_gz, "wb")
gzf.write(in_data)
gzf.close()

end = time.time()
print('execution time' + str(end - start))